### AITech — Uczenie maszynowe — laboratoria
# 10. Sieci neuronowe (PyTorch)

Przykład implementacji sieci neuronowej do rozpoznawania cyfr ze [zbioru MNIST](https://en.wikipedia.org/wiki/MNIST_database), według https://github.com/pytorch/examples/tree/master/mnist

In [1]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torchvision import datasets, transforms
from torch.optim.lr_scheduler import StepLR


class Net(nn.Module):
    """W PyTorchu tworzenie sieci neuronowej
    polega na zdefiniowaniu klasy, która dziedziczy z nn.Module.
    """
    
    def __init__(self):
        super().__init__()
        
        # Warstwy splotowe
        self.conv1 = nn.Conv2d(1, 32, 3, 1)
        self.conv2 = nn.Conv2d(32, 64, 3, 1)
        
        # Warstwy dropout
        self.dropout1 = nn.Dropout(0.25)
        self.dropout2 = nn.Dropout(0.5)
        
        # Warstwy liniowe
        self.fc1 = nn.Linear(9216, 128)
        self.fc2 = nn.Linear(128, 10)

    def forward(self, x):
        """Definiujemy przechodzenie "do przodu" jako kolejne przekształcenia wejścia x"""
        x = self.conv1(x)
        x = F.relu(x)
        x = self.conv2(x)
        x = F.relu(x)
        x = F.max_pool2d(x, 2)
        x = self.dropout1(x)
        x = torch.flatten(x, 1)
        x = self.fc1(x)
        x = F.relu(x)
        x = self.dropout2(x)
        x = self.fc2(x)
        output = F.log_softmax(x, dim=1)
        return output


def train(model, device, train_loader, optimizer, epoch, log_interval, dry_run):
    """Uczenie modelu"""
    model.train()
    for batch_idx, (data, target) in enumerate(train_loader):
        data, target = data.to(device), target.to(device)  # wrzucenie danych na kartę graficzną (jeśli dotyczy)
        optimizer.zero_grad()  # wyzerowanie gradientu
        output = model(data)  # przejście "do przodu"
        loss = F.nll_loss(output, target)  # obliczenie funkcji kosztu
        loss.backward()  # propagacja wsteczna
        optimizer.step()  # krok optymalizatora
        if batch_idx % log_interval == 0:
            print('Train Epoch: {} [{}/{} ({:.0f}%)]\tLoss: {:.6f}'.format(
                epoch, batch_idx * len(data), len(train_loader.dataset),
                100. * batch_idx / len(train_loader), loss.item()))
            if dry_run:
                break


def test(model, device, test_loader):
    """Testowanie modelu"""
    model.eval()
    test_loss = 0
    correct = 0
    with torch.no_grad():
        for data, target in test_loader:
            data, target = data.to(device), target.to(device)  # wrzucenie danych na kartę graficzną (jeśli dotyczy)
            output = model(data)  # przejście "do przodu"
            test_loss += F.nll_loss(output, target, reduction='sum').item()  # suma kosztów z każdego batcha
            pred = output.argmax(dim=1, keepdim=True)  # predykcja na podstawie maks. logarytmu prawdopodobieństwa
            correct += pred.eq(target.view_as(pred)).sum().item()

    test_loss /= len(test_loader.dataset)  # obliczenie kosztu na zbiorze testowym

    print('\nTest set: Average loss: {:.4f}, Accuracy: {}/{} ({:.0f}%)\n'.format(
        test_loss, correct, len(test_loader.dataset),
        100. * correct / len(test_loader.dataset)))


def run(
        batch_size=64,
        test_batch_size=1000,
        epochs=14,
        lr=1.0,
        gamma=0.7,
        no_cuda=False,
        dry_run=False,
        seed=1,
        log_interval=10,
        save_model=False,
    ):
    """Main training function.
    
    Arguments:
        batch_size - wielkość batcha podczas uczenia (default: 64),
        test_batch_size - wielkość batcha podczas testowania (default: 1000)
        epochs - liczba epok uczenia (default: 14)
        lr - współczynnik uczenia (learning rate) (default: 1.0)
        gamma - współczynnik gamma (dla optymalizatora) (default: 0.7)
        no_cuda - wyłącza uczenie na karcie graficznej (default: False)
        dry_run - szybko ("na sucho") sprawdza pojedyncze przejście (default: False)
        seed - ziarno generatora liczb pseudolosowych (default: 1)
        log_interval - interwał logowania stanu uczenia (default: 10)
        save_model - zapisuje bieżący model (default: False)
    """
    use_cuda = no_cuda and torch.cuda.is_available()

    torch.manual_seed(seed)

    device = torch.device("cuda" if use_cuda else "cpu")

    train_kwargs = {'batch_size': batch_size}
    test_kwargs = {'batch_size': test_batch_size}
    if use_cuda:
        cuda_kwargs = {'num_workers': 1,
                       'pin_memory': True,
                       'shuffle': True}
        train_kwargs.update(cuda_kwargs)
        test_kwargs.update(cuda_kwargs)

    transform=transforms.Compose([
        transforms.ToTensor(),
        transforms.Normalize((0.1307,), (0.3081,))
        ])
    dataset1 = datasets.MNIST('../data', train=True, download=True,
                       transform=transform)
    dataset2 = datasets.MNIST('../data', train=False,
                       transform=transform)
    train_loader = torch.utils.data.DataLoader(dataset1,**train_kwargs)
    test_loader = torch.utils.data.DataLoader(dataset2, **test_kwargs)

    model = Net().to(device)
    optimizer = optim.Adadelta(model.parameters(), lr=lr)

    scheduler = StepLR(optimizer, step_size=1, gamma=gamma)
    for epoch in range(1, epochs + 1):
        train(model, device, train_loader, optimizer, epoch, log_interval, dry_run)
        test(model, device, test_loader)
        scheduler.step()

    if save_model:
        torch.save(model.state_dict(), "mnist_cnn.pt")

**Uwaga**: uruchomienie tego przykładu długo trwa. Żeby trwało krócej, można zmniejszyć liczbę epok.

In [2]:
run(epochs=5)

C:\Users\pawel\anaconda3\lib\site-packages\torch\autograd\__init__.py:130: UserWarning: CUDA initialization: The NVIDIA driver on your system is too old (found version 9020). Please update your GPU driver by downloading and installing a new version from the URL: http://www.nvidia.com/Download/index.aspx Alternatively, go to: https://pytorch.org to install a PyTorch version that has been compiled with your version of the CUDA driver. (Triggered internally at  ..\c10\cuda\CUDAFunctions.cpp:100.)
  Variable._execution_engine.run_backward(


Train Epoch: 1 [0/60000 (0%)]	Loss: 2.305400
Train Epoch: 1 [640/60000 (1%)]	Loss: 1.359776
Train Epoch: 1 [1280/60000 (2%)]	Loss: 0.842885
Train Epoch: 1 [1920/60000 (3%)]	Loss: 0.587047
Train Epoch: 1 [2560/60000 (4%)]	Loss: 0.368678
Train Epoch: 1 [3200/60000 (5%)]	Loss: 0.468111
Train Epoch: 1 [3840/60000 (6%)]	Loss: 0.264335
Train Epoch: 1 [4480/60000 (7%)]	Loss: 0.288264
Train Epoch: 1 [5120/60000 (9%)]	Loss: 0.579878
Train Epoch: 1 [5760/60000 (10%)]	Loss: 0.225971
Train Epoch: 1 [6400/60000 (11%)]	Loss: 0.235435
Train Epoch: 1 [7040/60000 (12%)]	Loss: 0.334189
Train Epoch: 1 [7680/60000 (13%)]	Loss: 0.205391
Train Epoch: 1 [8320/60000 (14%)]	Loss: 0.224400
Train Epoch: 1 [8960/60000 (15%)]	Loss: 0.265982
Train Epoch: 1 [9600/60000 (16%)]	Loss: 0.110670
Train Epoch: 1 [10240/60000 (17%)]	Loss: 0.266168
Train Epoch: 1 [10880/60000 (18%)]	Loss: 0.086807
Train Epoch: 1 [11520/60000 (19%)]	Loss: 0.417719
Train Epoch: 1 [12160/60000 (20%)]	Loss: 0.276456
Train Epoch: 1 [12800/60000 (

Train Epoch: 2 [44800/60000 (75%)]	Loss: 0.059499
Train Epoch: 2 [45440/60000 (76%)]	Loss: 0.109399
Train Epoch: 2 [46080/60000 (77%)]	Loss: 0.078003
Train Epoch: 2 [46720/60000 (78%)]	Loss: 0.111255
Train Epoch: 2 [47360/60000 (79%)]	Loss: 0.061806
Train Epoch: 2 [48000/60000 (80%)]	Loss: 0.039426
Train Epoch: 2 [48640/60000 (81%)]	Loss: 0.035167
Train Epoch: 2 [49280/60000 (82%)]	Loss: 0.027696
Train Epoch: 2 [49920/60000 (83%)]	Loss: 0.021057
Train Epoch: 2 [50560/60000 (84%)]	Loss: 0.040626
Train Epoch: 2 [51200/60000 (85%)]	Loss: 0.150808
Train Epoch: 2 [51840/60000 (86%)]	Loss: 0.026038
Train Epoch: 2 [52480/60000 (87%)]	Loss: 0.014357
Train Epoch: 2 [53120/60000 (88%)]	Loss: 0.030147
Train Epoch: 2 [53760/60000 (90%)]	Loss: 0.085780
Train Epoch: 2 [54400/60000 (91%)]	Loss: 0.028594
Train Epoch: 2 [55040/60000 (92%)]	Loss: 0.037993
Train Epoch: 2 [55680/60000 (93%)]	Loss: 0.070294
Train Epoch: 2 [56320/60000 (94%)]	Loss: 0.035509
Train Epoch: 2 [56960/60000 (95%)]	Loss: 0.022443


Train Epoch: 4 [28800/60000 (48%)]	Loss: 0.005579
Train Epoch: 4 [29440/60000 (49%)]	Loss: 0.010757
Train Epoch: 4 [30080/60000 (50%)]	Loss: 0.013080
Train Epoch: 4 [30720/60000 (51%)]	Loss: 0.004695
Train Epoch: 4 [31360/60000 (52%)]	Loss: 0.009816
Train Epoch: 4 [32000/60000 (53%)]	Loss: 0.097901
Train Epoch: 4 [32640/60000 (54%)]	Loss: 0.008036
Train Epoch: 4 [33280/60000 (55%)]	Loss: 0.025720
Train Epoch: 4 [33920/60000 (57%)]	Loss: 0.007743
Train Epoch: 4 [34560/60000 (58%)]	Loss: 0.010240
Train Epoch: 4 [35200/60000 (59%)]	Loss: 0.040739
Train Epoch: 4 [35840/60000 (60%)]	Loss: 0.046888
Train Epoch: 4 [36480/60000 (61%)]	Loss: 0.002148
Train Epoch: 4 [37120/60000 (62%)]	Loss: 0.018123
Train Epoch: 4 [37760/60000 (63%)]	Loss: 0.138039
Train Epoch: 4 [38400/60000 (64%)]	Loss: 0.092445
Train Epoch: 4 [39040/60000 (65%)]	Loss: 0.004439
Train Epoch: 4 [39680/60000 (66%)]	Loss: 0.059561
Train Epoch: 4 [40320/60000 (67%)]	Loss: 0.016702
Train Epoch: 4 [40960/60000 (68%)]	Loss: 0.048608


Polecam również bibliotekę [PyTorch-Lightning](https://www.pytorchlightning.ai), dzięki któej kod PyTorcha staje się trochę bardziej "uporządkowany".

Tutaj artykuł o tym, jak stworzyć dataloader dla danych z własnego pliku CSV: https://androidkt.com/load-pandas-dataframe-using-dataset-and-dataloader-in-pytorch

## Zadanie 10 (6 punktów)

Zaimplementuj rozwiązanie wybranego problemu klasyfikacyjnego za pomocą prostej sieci neuronowej stworzonej przy użyciu biblioteki PyTorch.